In [3]:
import gensim

from urllib import request 
import logging
from pathlib import Path
import numpy as np
import pandas as pd
import re
import MeCab
import random
from gensim import corpora, models

In [99]:
#snssns..set_styleset_sty ('whitegrid')
%matplotlib inline

pd.set_option("display.max_columns", 2000) # 表示カラムの最大値
pd.set_option('display.max_rows', 2000) # 表示行数の最大値
pd.set_option('display.max_colwidth', 300)
pd.set_option("display.float_format", '{:.3f}'.format) # 小数点以下の有効数字

# jupyterの幅を自動調整
from IPython.core.display import display, HTML
display(HTML("<style>.container { width:85% !important; }</style>"))

# 参考
- 【技術解説】単語の重要度を測る？TF-IDFとOkapi BM25の計算方法とは  
https://mieruca-ai.com/ai/tf-idf_okapi-bm25/  
   
- 日本語テキストのカテゴリをtf-idfとランダムフォレストで学習する〜livedoor ニュースを題材に  
https://qiita.com/kotaroito/items/bd5f5760a45152281b54

- 【python】TF-IDFで重要語を抽出してみる  
https://www.haya-programming.com/entry/2018/07/09/190819


# コーパス作成（定量変換前）

In [30]:
import glob

def load_livedoor_news_corpus():
    category = {
        'dokujo-tsushin': 1,
        'it-life-hack':2,
        'kaden-channel': 3,
        'livedoor-homme': 4,
        'movie-enter': 5,
        'peachy': 6,
        'smax': 7,
        'sports-watch': 8,
        'topic-news':9
    }
    docs  = []
    labels = []

    for c_name, c_id in category.items():
        files = glob.glob("../../../../../Desktop/自習/03.date/text/{c_name}/{c_name}*.txt".format(c_name=c_name))

        text = ''
        for file in files:
            with open(file, 'r',encoding='UTF-8') as f:#windows環境の場合のみ、encodingオプション必要
                lines = f.read().splitlines() 

                url = lines[0]
                datetime = lines[1]
                subject = lines[2]
                body = "\n".join(lines[3:])
                text = subject + "\n" + body

            docs.append(text)
            labels.append(c_id)

    return docs, labels

docs, labels = load_livedoor_news_corpus()

In [96]:
import glob

def load_livedoor_news_corpus():
    category = {
        'dokujo-tsushin': 1,
        'it-life-hack':2,
        'kaden-channel': 3,
        'livedoor-homme': 4,
        'movie-enter': 5,
        'peachy': 6,
        'smax': 7,
        'sports-watch': 8,
        'topic-news':9
    }
    docs  = []
    labels = []
    doc_id=[]
    doc_count = 0

    for c_name, c_id in category.items():
        files = glob.glob("../../../../../Desktop/自習/03.date/text/{c_name}/{c_name}*.txt".format(c_name=c_name))

        text = ''
        for file in files:
            with open(file, 'r',encoding='UTF-8') as f:#windows環境の場合のみ、encodingオプション必要
                lines = f.read().splitlines() 
                lines_notnull = [s for s in lines if s != '']
                doc_count += 1
                url = lines_notnull[0]
                datetime = lines_notnull[1]

                for line in lines_notnull[3:]:
                    doc_id.append(doc_count)
                    docs.append(line)
                    labels.append(c_id)
    doc_id_s = pd.Series(doc_id)
    docs_s = pd.Series(docs)
    labels_s = pd.Series(labels)
    df = pd.concat([doc_id_s,labels_s,docs_s],axis=1)
    df.columns = ['doc_id','label','docs']

    return df

df = load_livedoor_news_corpus()

In [110]:
df[(df['doc_id'])&(df['docs']!='')]

KeyError: 0

In [93]:
docs  = []
labels = []
doc_id=[]
doc_count = 0

files = glob.glob("../../../../../Desktop/自習/03.date/text/it-life-hack/it-life-hack-6292880.txt")
text = ''
for file in files:
    with open(file, 'r',encoding='UTF-8') as f:#windows環境の場合のみ、encodingオプション必要
        lines = f.read().splitlines() 
        lines_notnull = [s for s in lines if s != '']
        doc_count += 1
        url = lines_notnull[0]
        datetime = lines_notnull[1]

        for line in lines_notnull[3:]:
            doc_id.append(doc_count)
            docs.append(line)
            labels.append(c_id)

doc_id_s = pd.Series(doc_id)
docs_s = pd.Series(docs)
labels_s = pd.Series(labels)
df = pd.concat([doc_id_s,labels_s,docs_s],axis=1)
df.columns = ['doc_id','label','docs']

In [94]:
df

doc_id  label                           docs
0        1      1  テレビやTwitterと連携できるパソコンや、プロセ...
1        1      1  ■インテル SSD 520をMacに装着！旧式Mac...
2        1      1  インテルが最新SSD「520シリーズ」を発売した。現...
3        1      1  ■http://itlifehack.jp/arch...
4        1      1  ThinkPad X1 Hybridは使用するCPU...
5        1      1  ■初期費用、更新費用ともに無料！ジャストシステム、ヤ...
6        1      1  現在では、多くのユーザーがパソコンにセキュリティソフ...
7        1      1  ■テレビの新しい楽しみ方を提案！NECの春PCはTV...
8        1      1  NECは2012年2月14日、個人向けデスクトップパ...
9        1      1   ■まるでお祭りの出荷式！レッツノートSX1の出荷が始まる
10       1      1  2月24日に発売されるLet’snote SX1/N...
11       1      1  【エプソン純正インク】インクカートリッジ 6色セット...
12       1      1                           エプソン
13       1      1               販売元：Amazon.co.jp
14       1      1                        クチコミを見る

In [83]:
print(len(docs))   # 7367
print(len(labels)) # 7367

15
15


# 学習データとテストデータ分割

In [32]:
import random

## indices は 0〜7366 の整数をランダムに並べ替えた配列
random.seed()
indices = list(range(len(docs)))
random.shuffle(indices)

train_data   = [docs[i] for i in indices[0:7000]]
train_labels = [labels[i] for i in indices[0:7000]]
test_data    = [docs[i] for i in indices[7000:]]
test_labels  = [labels[i] for i in indices[7000:]]

# tf-idfベクトルの作成

In [37]:
from natto import MeCab
from sklearn.feature_extraction.text import TfidfVectorizer

def tokenize(text):
    tokens = []
    with MeCab('-F%f[0],%f[6]') as nm:
        for n in nm.parse(text, as_nodes=True):
            # ignore any end-of-sentence nodes
            if not n.is_eos() and n.is_nor():
                klass, word = n.feature.split(',', 1)
                if klass in ['名詞', '形容詞', '形容動詞', '動詞']:
                    tokens.append(word)

    return tokens

vectorizer = TfidfVectorizer(tokenizer=tokenize)
train_matrix = vectorizer.fit_transform(train_data)

# ランダムフォレスト

In [39]:
from sklearn.ensemble import RandomForestClassifier

test_matrix = vectorizer.transform(test_data)

clf2 = RandomForestClassifier(n_estimators=100)
clf2.fit(train_matrix, train_labels)

print(clf2.score(train_matrix, train_labels)) # 1.0
print(clf2.score(test_matrix, test_labels)) # 0.896457765668

1.0
0.8801089918256131


# 重要語抽出

In [82]:
fetch_20newsgroups()

{'data': ["From: lerxst@wam.umd.edu (where's my thing)\nSubject: WHAT car is this!?\nNntp-Posting-Host: rac3.wam.umd.edu\nOrganization: University of Maryland, College Park\nLines: 15\n\n I was wondering if anyone out there could enlighten me on this car I saw\nthe other day. It was a 2-door sports car, looked to be from the late 60s/\nearly 70s. It was called a Bricklin. The doors were really small. In addition,\nthe front bumper was separate from the rest of the body. This is \nall I know. If anyone can tellme a model name, engine specs, years\nof production, where this car is made, history, or whatever info you\nhave on this funky looking car, please e-mail.\n\nThanks,\n- IL\n   ---- brought to you by your neighborhood Lerxst ----\n\n\n\n\n",
  "From: guykuo@carson.u.washington.edu (Guy Kuo)\nSubject: SI Clock Poll - Final Call\nSummary: Final call for SI clock reports\nKeywords: SI,acceleration,clock,upgrade\nArticle-I.D.: shelley.1qvfo9INNc3s\nOrganization: University of Washingto

In [40]:
import numpy as np
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.datasets import fetch_20newsgroups

news20 = fetch_20newsgroups()
vectorizer = TfidfVectorizer(min_df=0.03)
tfidf_X = vectorizer.fit_transform(news20.data[:1000]).toarray()

index = tfidf_X.argsort(axis=1)[:,::-1]
feature_names = np.array(vectorizer.get_feature_names())
feature_words = feature_names[index]

n = 5  # top何単語取るか
m = 15  # 何記事サンプルとして抽出するか
for fwords, target in zip(feature_words[:m,:n], news20.target):
    # 各文書ごとにtarget（ラベル）とtop nの重要語を表示
    print(news20.target_names[target])
    print(fwords)

rec.autos
['car' 'was' 'this' 'the' 'where']
comp.sys.mac.hardware
['washington' 'add' 'guy' 'speed' 'call']
comp.sys.mac.hardware
['the' 'display' 'anybody' 'heard' 'disk']
comp.graphics
['division' 'chip' 'systems' 'computer' 'four']
sci.space
['error' 'known' 'tom' 'memory' 'the']
talk.politics.guns
['of' 'the' 'com' 'to' 'says']
sci.med
['thanks' 'couldn' 'instead' 'file' 'everyone']
comp.sys.ibm.pc.hardware
['chip' 'is' 'fast' 'ibm' 'bit']
comp.os.ms-windows.misc
['win' 'help' 'please' 'appreciated' 'figure']
comp.sys.mac.hardware
['the' 'file' 'lost' 've' 'it']
rec.motorcycles
['00' 'org' 'the' 'out' 'and']
talk.religion.misc
['the' 'that' 'may' 'to' 'is']
comp.sys.mac.hardware
['hp' 'co' 'com' 'tin' 'newsreader']
sci.space
['the' 'power' 'and' 'space' 'nasa']
misc.forsale
['10' 'very' 'and' 'reasonable' 'sale']


# livedoorニュースのカテゴリ毎に重要語を抽出する

In [43]:
news = pd.co

['友人代表のスピーチ、独女はどうこなしている？\n\u3000もうすぐジューン・ブライドと呼ばれる６月。独女の中には自分の式はまだなのに呼ばれてばかり……という「お祝い貧乏」状態の人も多いのではないだろうか？\u3000さらに出席回数を重ねていくと、こんなお願いごとをされることも少なくない。\n\n\u3000「お願いがあるんだけど……友人代表のスピーチ、やってくれないかな？」\n\n\u3000さてそんなとき、独女はどう対応したらいいか？\n\n\u3000最近だとインターネット等で検索すれば友人代表スピーチ用の例文サイトがたくさん出てくるので、それらを参考にすれば、無難なものは誰でも作成できる。しかし由利さん（33歳）はネットを参考にして作成したものの「これで本当にいいのか不安でした。一人暮らしなので聞かせて感想をいってくれる人もいないし、かといって他の友人にわざわざ聞かせるのもどうかと思うし……」ということで活用したのが、なんとインターネットの悩み相談サイトに。そこに作成したスピーチ文を掲載し「これで大丈夫か添削してください」とメッセージを送ったというのである。\n\n\u3000「一晩で3人位の人が添削してくれましたよ。ちなみに自分以外にもそういう人はたくさんいて、その相談サイトには同じように添削をお願いする投稿がいっぱいありました」（由利さん）。ためしに教えてもらったそのサイトをみてみると、確かに「結婚式のスピーチの添削お願いします」という投稿が1000件を超えるくらいあった。めでたい結婚式の影でこんなネットコミュニティがあったとは知らなかった。\n\n\u3000しかし「事前にお願いされるスピーチなら準備ができるしまだいいですよ。一番嫌なのは何といってもサプライズスピーチ！」と語るのは昨年だけで10万以上お祝いにかかったというお祝い貧乏独女の薫さん（35歳）\n\n\u3000「私は基本的に人前で話すのが苦手なんですよ。だからいきなり指名されるとしどろもどろになって何もいえなくなる。そうすると自己嫌悪に陥って終わった後でもまったく楽しめなくなりますね」\n\u3000\n\u3000サプライズスピーチのメリットとしては、準備していない状態なので、フランクな本音をしゃべってもらえるという楽しさがあるようだ。しかしそれも上手に対応できる人ならいいが、苦手な

In [44]:
labels

[1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
